In [2]:
import json
import pprint
import pandas as pd

In [14]:
with open('ner_output_v2_test_2.json') as f:
    json_data = json.load(f)

pprint.pp(json_data)

[{'Original Sentence': 'only his own group and the liberals support the '
                       'declaration but six groups have refused it.',
  'Original NER Instructions': "{'type': array(['QUANT', 'NORP'], "
                               "dtype=object), 'start': array([64, 27], "
                               "dtype=int32), 'length': array([3, 8], "
                               'dtype=int32)}',
  'Replaced Sentence': 'only his own team and the conservatives support the '
                       'declaration but three factions have rejected it.'},
 {'Original Sentence': 'the socialist position is much more complex.',
  'Original NER Instructions': "{'type': array(['NORP'], dtype=object), "
                               "'start': array([4], dtype=int32), 'length': "
                               'array([9], dtype=int32)}',
  'Replaced Sentence': 'the progressive stance is much more intricate.'},
 {'Original Sentence': 'mr duff for instance right now may want to put a '
         

In [16]:
#check if the word required has been changed:
def reverse_list(lists):
    new_list = []
    for i in lists:
        new_list.insert(0, i)
    return new_list

def replaced_words_proximity(start, length):
    end_idx = -1
    close_words = []
    for idx, i in enumerate(start):
        start_idx = i
        if start_idx == end_idx:
            close_words.append(idx)
        end_idx = start_idx + length[idx]
    return close_words

def closest_find(sentence, target_word, target_idx):
    length = 0
    prev_distance = 1000
    best_idx = 0
    for idx, i in enumerate(sentence.split()):
        length += len(i + " ")
        if i == target_word:
            distance = abs(target_idx - length)
            if distance < prev_distance:
                best_idx = length - len(i)
                prev_distance = distance
    return best_idx

non_replace_wrong = 0
replace_wrong = 0
non_replace_count = 0
replace_count = 0
collate_word_types = {}
for each in json_data:
    original_text = each.get("Original Sentence")
    og_end = len(original_text) - 1

    replaced_text = each.get("Replaced Sentence")
    replaced_end = len(replaced_text)
    instruction = each.get("Original NER Instructions")
    instruction = instruction.replace("array(", "")
    instruction = instruction.replace(", dtype=object)","")
    instruction = instruction.replace(",dtype=object)","")
    instruction = instruction.replace(", dtype=int32)", "")
    instruction = instruction.replace(")", "")
    instruction = instruction.replace("\'", "\"")
    instruction = json.loads(instruction)

    types = reverse_list(instruction.get("type"))
    start = reverse_list(instruction.get("start"))
    length = reverse_list(instruction.get("length"))

    if types == []:
        non_replace_count += 1
        if original_text != replaced_text:
            non_replace_wrong += 1
    else:
        check_proximity = replaced_words_proximity(start, length)
        for idx, i in enumerate(length):
            start_idx = start[idx]
            end_idx = start_idx + i
            unchanged_front = original_text[0:start_idx-1].split()[-1]
            original_tbc = original_text[start_idx:end_idx]
            if check_proximity == []:
                start_replaced_idx = closest_find(replaced_text, unchanged_front, start_idx) + len(unchanged_front)
                edit_replaced_text = replaced_text[start_replaced_idx:len(replaced_text)-1]
            elif idx in check_proximity:
                start_replaced_idx = replaced_text.find(changed_text) + len(changed_text)
                edit_replaced_text = replaced_text[start_replaced_idx:len(replaced_text)-1]
            if original_text[end_idx:og_end].split() != []:
                unchanged_back = original_text[end_idx:og_end].split()[0]
                end_replaced_idx = edit_replaced_text.find(unchanged_back)
                changed_text = edit_replaced_text[0:end_replaced_idx-1]
            if types[idx] in collate_word_types.keys():
                new = collate_word_types.get(types[idx])
                new.append(changed_text)
                collate_word_types[types[idx]] = new
            else:
                collate_word_types[types[idx]] = [changed_text]
            replace_count += 1
            if original_tbc == changed_text:
                replace_wrong += 1
accuracy = 100 - (replace_wrong + non_replace_wrong)/(replace_count + non_replace_count)*100
print(f'accuracy = {accuracy}%')
print(f'Non replacement wrongs = {non_replace_wrong}/{non_replace_count}')
print(f'Replacement wrongs = {replace_wrong}/{replace_count}')

accuracy = 78.66127583108715%
Non replacement wrongs = 71/637
Replacement wrongs = 404/1589


Second v2 Test = 79.57038391224863%
Non replacement wrongs = 104/643
Replacement wrongs = 343/1545

In [16]:
with open('ner_output_v1_train_test_3.json') as f:
    json_data = json.load(f)

pprint.pp(json_data)

[{'Original Sentence': 'it has taken a long time for there to be eu action but '
                       "i'm very glad that we found broad consensus to update "
                       'the dual use regulation that will tackle this toxic '
                       'trade with targeted measures on the basis of human '
                       'security.',
  'Original NER Instructions': 'Replace the PLACE ner type word, starting from '
                               'character 41 to character 42, with a '
                               'dissimilar word.',
  'Replaced Sentence': 'it has taken a long time for there to be us action but '
                       "i'm very glad that we found broad consensus to update "
                       'the dual use regulation that will tackle this toxic '
                       'trade with targeted measures on the basis of human '
                       'security.'},
 {'Original Sentence': 'we have had enough high level meetings.',
  'Original NER Instructio

In [27]:
#check if the word required has been changed:
def reverse_list(lists):
    new_list = []
    for i in lists:
        new_list.insert(0, i)
    return new_list

def replaced_words_proximity(start, end):
    end_idx = -1
    close_words = []
    for idx, i in enumerate(start):
        start_idx = i
        if start_idx == end_idx:
            close_words.append(idx)
        end_idx = int(end[idx]) + 1
    return close_words

def closest_find(sentence, target_word, target_idx):
    length = 0
    prev_distance = 1000
    best_idx = 0
    for idx, i in enumerate(sentence.split()):
        length += len(i + " ")
        if i == target_word:
            distance = abs(target_idx - length)
            if distance < prev_distance:
                best_idx = length - len(i)
                prev_distance = distance
    return best_idx

non_replace_wrong = 0
replace_wrong = 0
non_replace_count = 0
replace_count = 0
collate_word_types = {}
remove_list = ["Replace", "wordReplace", "the", "ner", "type", "word", "starting", "from", "character", "to", ",", "with", "a", "dissimilar", ".", "give", "me", "replaced", "sentence", "based", "on", "original", "word'Replace"]
for each in json_data:
    original_text = each.get("Original Sentence")
    og_end = len(original_text) - 1
    replaced_text = each.get("Replaced Sentence")
    og_instruction = each.get("Original NER Instructions")
    og_instruction = og_instruction.replace(",", "")
    og_instruction = og_instruction.replace(".", "")
    og_instruction = og_instruction.replace(":", "")
    og_instruction = og_instruction.split(" ")
    instruction = [word for word in og_instruction if word not in remove_list]
    itr_count = 0
    types = []
    start = []
    end = []
    for i in instruction:
        if itr_count == 0:
            types.append(i)
            itr_count += 1
        elif itr_count == 1:
            start.append(i)
            itr_count += 1
        else:
            end.append(i)
            itr_count = 0
        
    types = reverse_list(types)
    start = reverse_list(start)
    end = reverse_list(end)

    if types == ['']:
        non_replace_count += 1
        if original_text != replaced_text.lower():
            non_replace_wrong += 1
            print(original_text)
            print(replaced_text)
    else:
        check_proximity = replaced_words_proximity(start, end)
        for idx, i in enumerate(end):
            start_idx = int(start[idx])
            end_idx = int(i)
            unchanged_front = original_text[0:start_idx-1].split()[-1]
            original_tbc = original_text[start_idx:end_idx]
            if check_proximity == []:
                start_replaced_idx = closest_find(replaced_text, unchanged_front, start_idx) + len(unchanged_front)
                edit_replaced_text = replaced_text[start_replaced_idx:len(replaced_text)-1]
            elif idx in check_proximity:
                start_replaced_idx = replaced_text.find(changed_text) + len(changed_text)
                edit_replaced_text = replaced_text[start_replaced_idx:len(replaced_text)-1]
            if original_text[end_idx:og_end].split() != []:
                unchanged_back = original_text[end_idx:og_end].split()[0]
                end_replaced_idx = edit_replaced_text.find(unchanged_back)
                changed_text = edit_replaced_text[0:end_replaced_idx-1]
            if types[idx] in collate_word_types.keys():
                new = collate_word_types.get(types[idx])
                new.append(changed_text)
                collate_word_types[types[idx]] = new
            else:
                collate_word_types[types[idx]] = [changed_text]
            replace_count += 1
            if original_tbc == changed_text:
                replace_wrong += 1
accuracy = 100 - (replace_wrong + non_replace_wrong)/(replace_count + non_replace_count)*100
print(f'accuracy = {accuracy}%')
print(f'Non replacement wrongs = {non_replace_wrong}/{non_replace_count}')
print(f'Replacement wrongs = {replace_wrong}/{replace_count}')

although as there has been some confusion today on whether there will actually now be an investigation a reassurance from the commission is necessary that this is going to be the case. the ecr group has long argued for further action at national eu and global level to tackle tax evasion tax fraud and indeed aggressive tax avoidance.
although as there has been some confusion today on whether there will actually now be an investigation a reassurance from the commission is necessary that this is going to be the case. the group has long argued for further action at national continental and global level to tackle tax evasion tax fraud and indeed aggressive tax avoidance.
it is also clear that if we want the eu two thousand and twenty process the semester to have democratic legitimacy we need to involve civil society and social partners much more strongly.
it is also clear that if we want the global twenty twenty process the semester to have democratic legitimacy we need to involve civil soc

accuracy = 95.62234563868017%
Non replacement wrongs = 264/1610
Replacement wrongs = 4/4512

Replace the PLACE ner type word, starting from character 41 to character 42, with a dissimilar word.
['PLACE', '41', '42']

['']

['']
Replace the PLACE ner type word, starting from character 174 to character 175, with a dissimilar word.'Replace the ORG ner type word, starting from character 57 to character 78, with a dissimilar word.'Replace the WHEN ner type word, starting from character 4 to character 34, with a dissimilar word.
['PLACE', '174', '175', "word'Replace", 'ORG', '57', '78', "word'Replace", 'WHEN', '4', '34']
Replace the ORG ner type word, starting from character 38 to character 60, with a dissimilar word.
['ORG', '38', '60']

['']
Replace the PLACE ner type word, starting from character 64 to character 69, with a dissimilar word.
['PLACE', '64', '69']

['']
Replace the WHEN ner type word, starting from character 120 to character 128, with a dissimilar word.'Replace the WHEN ner type word, starting from character 48 to character 87, with a dissimilar word.'Replace the ORG ner type word, starting from character 33 to character 38, with a dissimilar word.
['WHEN', '120', '128', "word'Replace", 'WHEN', '48', '87', "word'Replace", 'ORG', '33', '38']
Replace the ORG ner type word, starting from character 152 to character 155, with a dissimilar word.'Replace the QUANT ner type word, starting from character 107 to character 113, with a dissimilar word.'Replace the WHEN ner type word, starting from character 69 to character 88, with a dissimilar word.'Replace the PLACE ner type word, starting from character 3 to character 9, with a dissimilar word.
['ORG', '152', '155', "word'Replace", 'QUANT', '107', '113', "word'Replace", 'WHEN', '69', '88', "word'Replace", 'PLACE', '3', '9']
Replace the PLACE ner type word, starting from character 498 to character 503, with a dissimilar word.'Replace the PLACE ner type word, starting from character 439 to character 440, with a dissimilar word.'Replace the PLACE ner type word, starting from character 266 to character 279, with a dissimilar word.'Replace the QUANT ner type word, starting from character 186 to character 190, with a dissimilar word.'Replace the PLACE ner type word, starting from character 130 to character 131, with a dissimilar word.'Replace the PLACE ner type word, starting from character 39 to character 40, with a dissimilar word.
['PLACE', '498', '503', "word'Replace", 'PLACE', '439', '440', "word'Replace", 'PLACE', '266', '279', "word'Replace", 'QUANT', '186', '190', "word'Replace", 'PLACE', '130', '131', "word'Replace", 'PLACE', '39', '40']

['']
...
['WHEN', '61', '69']
accuracy = 87.57485029940119%
Non replacement wrongs = 264/1610
Replacement wrongs = 400/3734
Output is truncated. View as a scrollable element or open in a text editor. Adjust cell output settings...


although as there has been some confusion today on whether there will actually now be an investigation a reassurance from the commission is necessary that this is going to be the case. the ecr group has long argued for further action at national eu and global level to tackle tax evasion tax fraud and indeed aggressive tax avoidance.
although as there has been some confusion today on whether there will actually now be an investigation a reassurance from the commission is necessary that this is going to be the case. the group has long argued for further action at national continental and global level to tackle tax evasion tax fraud and indeed aggressive tax avoidance.
it is also clear that if we want the eu two thousand and twenty process the semester to have democratic legitimacy we need to involve civil society and social partners much more strongly.
it is also clear that if we want the global twenty twenty process the semester to have democratic legitimacy we need to involve civil society and social partners much more strongly.
the answer is no and this is why we have to make every effort possible to fight ebola at origin now and do it in the most aggressive way we
the answer is no and this is why we have to make every effort possible to fight ebola at origin now and do it in the most aggressive way we.
on the contrary collective redress could provide efficient dispute resolution and the means to eliminate unreasonable barriers to access to justice in crossborder cases.
On the contrary, collective redress could provide efficient dispute resolution and the means to eliminate unreasonable barriers to access to justice in cross-border cases.
however the freedom to provide services must also be respected.
However, the freedom to provide services must also be respected.
the commission has set up a state aid web based search tool which provides information on state aid cases and on block exemption cases recorded.
The commission has set up a state aid web-based search tool which provides information on state aid cases and on block exemption cases recorded.
this is what our citizens expect from us namely that we take human rights very seriously in this kind of trade.
This is what our citizens expect from us, namely that we take human rights very seriously in this kind of trade.
we all agree that multiple compensation for the same harm should be avoided and the directive includes provision to achieve this goal. at the same time the text regulates interaction between the public and private enforcement of competition law leading to an optimal overall enforcement of competition rules.
We all agree that multiple compensation for the same harm should be avoided and the directive includes provision to achieve this goal. At the same time, the text regulates interaction between the public and private enforcement of competition law leading to an optimal overall enforcement of competition rules.
internal energy market package the importance of the citizen in the internal energy market has been elevated considerably. the new measures are intended to improve the operation of the retail energy market and provide additional consumer protection. these topics are discussed and followed up at the citizens' energy forum established with the aim of improving the functioning of the retail
Internal energy market package the importance of the citizen in the internal energy market has been elevated considerably. The new measures are intended to improve the operation of the retail energy market and provide additional consumer protection. These topics are discussed and followed up at the citizens' energy forum established with the aim of improving the functioning of the retail.
of course the ingredient constituent argument has arisen due to the labelling implications of each option. if pollen continues to be considered a constituent' any gm pollen present would not need to be labelled.
Of course, the ingredient constituent argument has arisen due to the labelling implications of each option. If pollen continues to be considered a constituent, any GM pollen present would not need to be labelled.
we should focus on completing the single market promote entrepreneurs and make way for growth and prosperity.
We should focus on completing the single market, promote entrepreneurs and make way for growth and prosperity.
once again we are expanding and strengthening its remit.
Once again, we are expanding and strengthening its remit.
the launch of the common steps towards visa free travel opens the prospect of visas being abolished and there was consensus at the summit that we should reinvigorate negotiations on a new agreement.
The launch of the common steps towards visa-free travel opens the prospect of visas being abolished and there was consensus at the summit that we should reinvigorate negotiations on a new agreement.
this may seem trivial when compared to the plight of so many people in the world but the point i am trying to make is that human rights are in danger everywhere;
This may seem trivial when compared to the plight of so many people in the world but the point I am trying to make is that human rights are in danger everywhere.
but both bodies suffer from the same problem a lack of credibility double standards at times and they are not able to act quickly enough.
But both bodies suffer from the same problem, a lack of credibility, double standards at times, and they are not able to act quickly enough.
society. this type of response is of course most effective on a global scale where it can be used to address global challenges such as the fight against poverty. this is a message i will push strongly for in
Society. This type of response is of course most effective on a global scale where it can be used to address global challenges such as the fight against poverty. This is a message I will push strongly for in.
however food packaging has led to a reduction in food wastage.
However, food packaging has led to a reduction in food wastage.
i also want to emphasise once again the need for unity of the people and a strict message of non violence.
I also want to emphasise once again the need for unity of the people and a strict message of non-violence.
sometimes as i said before this is for their own protection because let us be clear the reality out there on the ground is not ideal.
Sometimes, as I said before, this is for their own protection because let us be clear the reality out there on the ground is not ideal.
extreme poverty family breakdown and domestic violence contribute to some of the root causes of human trafficking.
Extreme poverty, family breakdown and domestic violence contribute to some of the root causes of human trafficking.
corporation taxes but also to introduce taxes based on wealth capital and turnover rather than profits and to challenge existing tax residency and transfer pricing rules.
Corporation taxes but also to introduce taxes based on wealth, capital and turnover rather than profits and to challenge existing tax residency and transfer pricing rules.
unfortunately as i said there have also been reasons for serious concern.
Unfortunately, as I said, there have also been reasons for serious concern.
we need to address the bad loan problem by ending the savage austerity agenda championed by this commission;
We need to address the bad loan problem by ending the savage austerity agenda championed by this commission.
as experience has shown in order to succeed a democratic transition needs strong political will from the authorities but also an effective and organised civil society.
As experience has shown, in order to succeed, a democratic transition needs strong political will from the authorities but also an effective and organised civil society.
for my group this proposal is far too unspecific in the aims it should reach for member states and could thus become a tool to impose unwanted structural reforms in the member states rather than supporting member states in difficult situations.
For my group, this proposal is far too unspecific in the aims it should reach for member states and could thus become a tool to impose unwanted structural reforms in the member states rather than supporting member states in difficult situations.
with this new mechanism the commission aims to remedy the current weaknesses as referred to by the rapporteur.
With this new mechanism, the commission aims to remedy the current weaknesses as referred to by the rapporteur.
the commission is committed to doing its share of the work for example making our own rulebook more business friendly; completing the integration of networks;
The commission is committed to doing its share of the work for example making our own rulebook more business friendly; completing the integration of networks.
the role of asset recovery has been acknowledged as an integral part of the fight against serious and organised cross border crime.
The role of asset recovery has been acknowledged as an integral part of the fight against serious and organised cross-border crime.
let me outline some
Let me outline some.
the commission does not have any enforcement powers;
The commission does not have any enforcement powers.
finally an e learning platform specifically designed for smes is planned to go on line in.
Finally an e-learning platform specifically designed for SMEs is planned to go online.
since we face the existential over arching challenge of increasing divergences.
Since we face the existential overarching challenge of increasing divergences.
so far. before i conclude i would like to highlight that much still remains to
So far. Before I conclude I would like to highlight that much still remains to.
you are nationalistic;
You are nationalistic.
the commission has also made its point on the so called fiscal multipliers in stressing the need for an intelligent composition of fiscal consolidation measures. for member states that have lost access to financial markets there is simply no choice;
The commission has also made its point on the so-called fiscal multipliers in stressing the need for an intelligent composition of fiscal consolidation measures. For member states that have lost access to financial markets there is simply no choice.
the new fund will focus its activities in particular in the north of the country supporting the health and energy sectors.
The new fund will focus its activities in particular in the south of the country supporting the health and energy sectors.
this is again a slight improvement.
this is again a minor enhancement.
securing a good balance between research in support of policy and more basic research reinforcing social science in the work programmes promoting dissemination of results and encouraging more coordination between national research programmes.
Securing a good balance between research in support of strategy and more fundamental research reinforcing social science in the work programmes promoting dissemination of results and encouraging more coordination between regional research programmes.
they look attractive on the surface but once these fraudulent companies get your credit card details you are wide open to fraud and exploitation.
They look appealing on the surface but once these deceptive firms get your credit card details you are wide open to fraud and exploitation.
as a large country it was able to demand and get those few extra crumbs from the table but that in the final analysis is all it amounts to.
As a significant nation it was able to demand and get those few extra crumbs from the table but that in the final analysis is all it amounts to.
at the same time i believe that it is also important to ensure the credibility and further reinforce the independence and objectivity of all our technical work not only in terms of economic preparations but also in terms of the independent collection of statistical
At the same time I believe that it is also important to ensure the credibility and further reinforce the independence and objectivity of all our technical work not only in terms of economic preparations but also in terms of the independent collection of statistical.
transparency is crucial to all
Transparency is crucial to all.
so back to you as a financial person how do you manage the financial transition to make sure that you can afford the investments now to get to cheap energy tomorrow?
So back to you as a financial individual how do you manage the financial transition to make sure that you can afford the investments now to get to cheap energy tomorrow?
it increases the functionality capacity and performance of the system and it also improves governance and accountability through greater safeguards on data protection. so i believe that once the system is in place and operational we will all benefit from the high quality of reliable services and the new information which
It increases the functionality capacity and performance of the system and it also improves governance and accountability through greater safeguards on data protection. So I believe that once the system is in place and operational we will all benefit from the high quality of reliable services and the new information which.
there are histories in different member states; there is the reputation issue;
There are histories in different member states; there is the reputation issue.
but let me make some things very clear the announcement of charges and the threat of imprisonment against the leader of the opposition in the country the leader of the sister party of the group of parties which i represent in this chamber is a dangerous moment for democracy in this country.
But let me make some things very clear the announcement of charges and the threat of imprisonment against the leader of the opposition in the region the leader of the sister party of the group of parties which I represent in this chamber is a dangerous moment for democracy in this region.
we need to complete the internal market;
We need to complete the internal market.
on the other hand this is a part of the world which has a long tradition of animosity springing out of a shared but contested history.
On the other hand this is a part of the globe which has a long tradition of animosity springing out of a shared but contested history.
the obsession that you will use the crisis to build a united states of europe.
The obsession that you will use the crisis to build a united states of Asia.
we want passengers to be taken home or to where they want to
We want passengers to be taken home or to where they want to.
have been. together we are emerging from the crisis united open and i believe
have been. together we are emerging from the crisis united open and i believe.
interesting. i am not a fan of the intergovernmental method but he is proposing something which is highly intergovernmental so that is
interesting. i am not a fan of the intergovernmental method but he is proposing something which is highly intergovernmental so that is.
such as project bonds the connecting europe facility and the possibility of anticipating some of the proposals for the next multiannual financial framework so that we can also show our citizens that we are serious when we speak about the possibilities of growth and are ready to make some kind of public
such as project bonds the connecting europe facility and the possibility of anticipating some of the proposals for the next multiannual financial framework so that we can also show our citizens that we are serious when we speak about the possibilities of growth and are ready to make some kind of public.
this will happen through inter alia the decoupling of the access rights payments and the payments for sectoral support. we are going to decouple
this will happen through inter alia the decoupling of the access rights payments and the payments for sectoral support. we are going to decouple.
the text in front of you is fully in line with the outcome of the trilogue and is fully supported by the commission.
the text in front of you is fully in line with the outcome of the trilogue and is fully supported by the organization.
his arrest and imprisonment follows repeated acts of intimidation and harassment conducted by the authorities against journalists.
his arrest and imprisonment follows repeated acts of intimidation and harassment conducted by the officials against journalists.
i fear it will invite retaliation and encourage protectionism around the world.
i fear it will invite retaliation and encourage protectionism around the globe.
we have thrown money at problems.
we have thrown resources at problems.
regarding current account surpluses the commission is carrying out a horizontal analysis on the policy implications of large and sustained current account surpluses;
regarding current account surpluses the organization is carrying out a horizontal analysis on the policy implications of large and sustained current account surpluses;
they will have a field day here because there is so much simplification needed.
they will have a field day here because there is so much streamlining needed.
one. there is no single solution to this crisis. we need to address all issues to fight the root causes to support and cooperate with the neighbouring countries to better protect our borders to fight smugglers with all the means we have to increase the reception capacities in the countries most affected and to ensure solidarity when it comes to finding for them a safe
one. there is no single solution to this crisis. we need to address all issues to fight the root causes to support and cooperate with the neighbouring countries to better protect our borders to fight smugglers with all the means we have to increase the reception capacities in the countries most affected and to ensure solidarity when it comes to finding for them a safe.
all. while i believe it is right that we also have expectations of others we must be ready to play our full part by presenting our clear political commitment to
all. while i believe it is right that we also have expectations of others we must be ready to play our full part by presenting our clear political commitment to.
we will work in particular with data protection authorities to ensure a uniform application of the rules.
we will work in particular with data protection officials to ensure a uniform application of the rules.
why should they book flights?
why should they reserve flights?
i think that the commission is of the same view and i would like to thank the commission for its quick reaction when providing us with its understanding of the issues raised in our question. while drafting this question we have been motivated by the fact
i think that the organization is of the same view and i would like to thank the organization for its quick reaction when providing us with its understanding of the issues raised in our question. while drafting this question we have been motivated by the fact.
please! colleagues i have got to ask for order in the
please! colleagues i have got to ask for order in the.
impact. the president of the commission and i both have this experience.
impact. the leader of the organization and i both have this experience.
they have no time to lose.
they have no time to waste.
that is why i want to state again that some of the proposals which were put forward are indeed themselves interesting ones but they are not able at this moment to generate the necessary consensus and the commission has to be very attentive to the contribution it gives to forging this consensus.
that is why i want to state again that some of the proposals which were put forward are indeed themselves interesting ones but they are not able at this moment to generate the necessary consensus and the organization has to be very attentive to the contribution it gives to forging this consensus.
for that reason the concerns especially of our coastal communities and their mainly small vessels fishing within quota have to be taken into consideration and
for that reason the concerns especially of our coastal communities and their mainly small vessels fishing within quota have to be taken into consideration and.
body. we clearly support giving developing countries a stronger voice and participation in the definition of the global tax governance agenda without necessarily creating yet another intergovernmental
body. we clearly support giving developing countries a stronger voice and participation in the definition of the global tax governance agenda without necessarily creating yet another intergovernmental.
turning to the issue of migration and refugees again a similar
turning to the issue of migration and refugees again a similar.
since we believe it is important to have a permanent stability mechanism the commission played a constructive role supporting this limited revision of the treaty.
Since we believe it is important to have a permanent stability mechanism, the commission played a constructive role supporting this limited revision of the treaty.
in an increasingly digitalised world almost all the personal details of people's lives are held on a database somewhere and the protection of that information becomes increasingly important.
In an increasingly digitalised world, almost all the personal details of people's lives are held on a database somewhere and the protection of that information becomes increasingly important.
we all work in the same direction sound budgets lower debts sustainable
We all work in the same direction: sound budgets, lower debts, sustainable.
the rural development policy also foresees possibilities to help men and women to balance family and professional life. for example under the basic services measure social facilities like day care centres for children or elderly people can be supported. in addition local transport services and small scale infrastructure are eligible for support. the situation in rural areas is very diverse across member states including
The rural development policy also foresees possibilities to help men and women to balance family and professional life. For example, under the basic services measure, social facilities like day care centres for children or elderly people can be supported. In addition, local transport services and small-scale infrastructure are eligible for support. The situation in rural areas is very diverse across member states including.
we are also looking at innovative financing instruments such as insurance pooling to share risks. effective investments in disaster prevention will help to save lives limit damages and ultimately save money.
We are also looking at innovative financing instruments such as insurance pooling to share risks. Effective investments in disaster prevention will help to save lives, limit damages and ultimately save money.
human capital investments financed by the esf form an essential component of this policy mix in the context of the global knowledge based economy.
Human capital investments financed by the ESF form an essential component of this policy mix in the context of the global knowledge-based economy.
there are children in my own region who are trafficked but we find that even after registration with social services many trafficked children just disappear because they remain under the control of their traffickers. they find it just too easy to re traffic these children.
There are children in my own region who are trafficked but we find that even after registration with social services many trafficked children just disappear because they remain under the control of their traffickers. They find it just too easy to re-traffick these children.
investing in energy efficiency measures can bring about immediate and tangible benefits for both households and business in industry such as reduction of costs creation of employment opportunities and growth as well as an encouragement in the transition towards a low carbon economy.
Investing in energy efficiency measures can bring about immediate and tangible benefits for both households and business in industry such as reduction of costs, creation of employment opportunities and growth as well as an encouragement in the transition towards a low carbon economy.
we cannot have a common currency and a common monetary policy and leave everything else to the states
We cannot have a common currency and a common monetary policy and leave everything else to the states.
i would remind him that democracy is a method whereby you vote for people who govern you and then if you do not like what they do you can get rid of them turf them out and put somebody else in.
I would remind him that democracy is a method whereby you vote for people who govern you and then if you do not like what they do you can get rid of them, turf them out and put somebody else in.
moreover with the aim of addressing all these deficiencies a new mechanism a trust account the cas was introduced as a temporary measure.
Moreover, with the aim of addressing all these deficiencies, a new mechanism, a trust account, was introduced as a temporary measure.
well it is through the handling of infected chimpanzees gorillas monkeys porcupines but at the moment we are not seeing it as a danger for the rest of the world because we are not seeing that kind of movement of products. also
Well, it is through the handling of infected chimpanzees, gorillas, monkeys, porcupines, but at the moment we are not seeing it as a danger for the rest of the world because we are not seeing that kind of movement of products. Also.
its information assists mariners aircraft and emergency planners from a range of real time sources around the world but we need more than these sorts of facilities.
Its information assists mariners, aircraft and emergency planners from a range of real-time sources around the world but we need more than these sorts of facilities.
smes. tax systems should be simplified further and the tax burden redirected away from labour. we should be more resource and energy efficient and invest more in research innovation and development. because we cannot afford to sit back and
SMEs. Tax systems should be simplified further and the tax burden redirected away from labour. We should be more resource and energy efficient and invest more in research, innovation and development. Because we cannot afford to sit back and.
that is not to say that i do not think we need any of course we do we do need a framework but i would like to make an appeal for that to be as light as possible in the sense of setting member states' targets and allowing them to use their own best efforts to meet those.
That is not to say that I do not think we need any; of course we do, we do need a framework, but I would like to make an appeal for that to be as light as possible in the sense of setting member states' targets and allowing them to use their own best efforts to meet those.
we must not look negatively on the need to reduce the impact of transport on our environment but rather see it as an opportunity because jobs can be created in the r d sector while at the same time we are meeting our environmental targets.
We must not look negatively on the need to reduce the impact of transport on our environment but rather see it as an opportunity because jobs can be created in the R&D sector while at the same time we are meeting our environmental targets.
good policies trade innovation policies and other non financial resources will be just as crucial.
Good policies, trade innovation policies and other non-financial resources will be just as crucial.
we must do what we can but trade ministers at the national level as well as parliaments are perhaps the best positioned to address sector specific and regional elements of trade.
We must do what we can but trade ministers at the national level as well as parliaments are perhaps the best positioned to address sector-specific and regional elements of trade.
we have discussed the issues which are in the forefront of citizens' minds public services wages unemployment poverty and education. these are issues of concern to all of us since they affect all our citizens irrespective of their home country.
We have discussed the issues which are in the forefront of citizens' minds: public services, wages, unemployment, poverty and education. These are issues of concern to all of us since they affect all our citizens irrespective of their home country.
market to the benefit of individual consumers. the forum involving the representatives of consumers industry national energy regulators and national administrations seeks to improve implementation of energy legislation and may develop elements for codes of conduct with self regulating and even quasi binding effects
market to the benefit of individual consumers. the forum involving the representatives of consumers industry national energy regulators and national administrations seeks to improve implementation of energy legislation and may develop elements for codes of conduct with self regulating and even quasi binding effects.
happening. of course a fairer distribution of income would also give more money to those who would spend it and create new jobs especially
happening. of course a fairer distribution of income would also give more money to those who would spend it and create new jobs especially.
laying down general provisions on the european regional development fund the european social fund and the cohesion fund.
laying down general provisions on the federation regional development fund the federation social fund and the cohesion fund.
alarming. military action in line with international law is necessary but it is not enough. it needs to be part of the wider effort comprising measures in the political and diplomatic counter terrorism and terrorism funding humanitarian and communication
alarming. military action in line with international law is necessary but it is not enough. it needs to be part of the wider effort comprising measures in the political and diplomatic counter terrorism and terrorism funding humanitarian and communication.
he announced he would have the list of members of this expert group published along with all relevant documents including agendas and minutes of each meeting.
he announced he would have the list of participants of this advisory team published along with all pertinent documents including schedules and records of each gathering.
life. i think that is probably
existence. i think that is likely.
stronger consumer transparency and choice is building new opportunities for trustful secure and consumer friendly products and services.
enhanced buyer clarity and options is creating new possibilities for reliable safe and buyer friendly products and services.
people are slaughtered and buried in mass graves while the families are forced to state that these murders were the work of so called thugs.
individuals are killed and interred in large pits while the relatives are compelled to declare that these killings were the work of so-called criminals.
i hope that we can all unite in calling for the cutting of red tape and the increasing of business opportunities to create jobs and let our companies thrive.
i hope that we can all unite in calling for the cutting of red tape and the increasing of business opportunities to create jobs and let our enterprises thrive.
which will be applied equally in every member state.
which will be applied uniformly in every member region.
in any case i can assure you that we continue to work on this working with a regional and local focus to facilitate efsi support across the
in any case i can assure you that we continue to work on this working with a regional and local focus to facilitate efsi support across the.
they need to know that whatever the commission concludes is the result of an independent thorough and public proper inquiry.
they need to know that whatever the board concludes is the result of an independent thorough and public proper inquiry.
the aim of the regulation is precisely to ensure that nutrition and health claims made on foods are truthful clear and based on generally accepted scientific evidence so that the consumer is adequately protected.
the aim of the directive is precisely to ensure that nutrition and health claims made on foods are truthful clear and based on generally accepted scientific evidence so that the buyer is adequately protected.
from the commission side i can tell you that we are working with all we have to make the budget deliver more bigger and better results for our people to stretch every
from the board side i can tell you that we are working with all we have to make the budget deliver more larger and better results for our people to stretch every.
together with this strategy we adopted a new directive on port reception facilities which goes a long way ensuring that waste is brought back to land instead of being discharged at sea.
together with this strategy we adopted a new guideline on port reception facilities which goes a long way ensuring that waste is brought back to land instead of being discharged at ocean.
the commission is now working on the proposals i presented in my state of the union address and in my announcement to this house of the commission's roadmap to stability and growth.
the board is now working on the proposals i presented in my state of the union address and in my announcement to this assembly of the board's roadmap to stability and growth.
revision of the treaty you know what was the position of the commission.
revision of the agreement you know what was the position of the board.
although we have come a long way it is still of vital importance that the legislation that is in place for businesses as well as consumers is effective.
although we have come a long way it is still of vital importance that the directive that is in place for businesses as well as buyers is effective.
these journalists are not alone in facing repression.
these reporters are not alone in facing oppression.
we also need a more flexible budget to deal with crises as they arise.
we also need a more adaptable budget to deal with crises as they arise.
however a note of caution the idea that member states should no longer have to cofinance projects with any of their own money seems a high risk policy.
however a note of caution the idea that member regions should no longer have to cofinance projects with any of their own money seems a high risk policy.
it explicitly encourages more proactive measures to tackle this scourge.
it explicitly encourages more proactive measures to tackle this menace.
so for example we should be spending more of the budget on structural funds to create investment in infrastructure and training projects.
so for instance we should be spending more of the budget on structural funds to create investment in infrastructure and training projects.
so gm pollen needs to be authorised before this amendment of the directive and after the amendment.
so xyz pollen needs to be authorised before this amendment of the directive and after the amendment.
what is the treaty basis for this exclusion?
what is the agreement basis for this exclusion?
those who argue that this is a threat to national sovereignty in my country ignore the reality that this actually is by consensus and unanimity.
those who argue that this is a threat to national sovereignty in my region ignore the reality that this actually is by consensus and unanimity.
it is not against the traditional family.
it is not against the conventional family.
let me remind this house also that in the economic field there are binding tools backed by sanctions. in the social field we still largely rely on the open method of coordination.
let me remind this assembly also that in the economic field there are binding tools backed by sanctions. in the social field we still largely rely on the open method of coordination.
this is also a chance for our work on human rights democracy and the rule of law.
this is also a chance for our work on human rights democracy and the rule of order.
we are approaching the end of an economic cycle.
we are approaching the conclusion of an economic cycle.
package. time is the politician's
bundle. time is the politician's.
the commission will not enforce the regulations on battery cages for hens which may well force producers who have complied out of business. so what is this about enforcement?
the board will not enforce the regulations on battery cages for hens which may well force producers who have complied out of business. so what is this about enforcement?
it is more than i received from her in relation to my view. we have to have respectful debate in this house where people hear each other's views and then we come to conclusions.
it is more than i received from her in relation to my view. we have to have respectful debate in this assembly where people hear each other's views and then we come to conclusions.
i am glad that your report takes into account many of its elements.
i am glad that your report takes into account many of its components.
this is what the country needs in order to address the current challenges.
this is what the region needs in order to address the current challenges.
we have made important concessions.
we have made significant concessions.
consumers and small companies especially have found it difficult to obtain compensation for the harm they suffered.
buyers and small enterprises especially have found it difficult to obtain compensation for the harm they suffered.
it will be the most important instrument for the next epidemic.
it will be the most important tool for the next outbreak.
since we want to reinforce stability i think it is important that we agree on this limited revision of the treaty.
since we want to reinforce stability i think it is important that we agree on this limited revision of the agreement.
although i will not sit in this seat again i know you are aware that i am keen to try sitting where you are.
although i will not sit in this position again i know you are aware that i am keen to try sitting where you are.
many of the issues in fact have to be dealt with at member state
many of the issues in fact have to be dealt with at regional level.
the impact that losses like these have on ecosystems is catastrophic.
the impact that losses like these have on environments is catastrophic.
but it took this positivist approach that there is nothing in the law because had there been an indication a definition of pollen in the law as we are determining now it would have decided otherwise.
but it took this positivist approach that there is nothing in the guideline because had there been an indication a definition of pollen in the guideline as we are determining now it would have decided otherwise.
that must come out.
that must emerge.
the new regulation will remove the differences between the current national data protection laws.
the new directive will remove the differences between the current national data protection guidelines.
we can and should have more ambition when it comes to micro plastics in detergents in detergents and cosmetics and single use plastics by building on the success of our legislation on plastic bags.
we can and should have more ambition when it comes to micro plastics in detergents in detergents and cosmetics and single use plastics by building on the success of our directive on plastic bags.
but again there will always be some sort of mechanism.
but again there will always be some sort of system.
we must however recognise the opportunities that our air industry and new air routes bring for jobs and growth in regional economies.
we must however recognise the opportunities that our aviation industry and new air routes bring for jobs and growth in regional economies.
finally i know that questions of accountability are always of utmost importance and so are questions of transparency.
finally i know that questions of accountability are always of utmost importance and so are questions of clarity.
we are certainly seeing that in my own country.
we are certainly seeing that in my own region.
of our party or personal views we are all parliamentarians and one of the most important powers we have is the ability to hold the executive to account through parliamentary pqs but these pqs are now being treated with contempt by the services. questions are not receiving proper answers they are evasive incomplete and dismissive and the timescale for answering is frequency exceeded. rule
of our party or personal views we are all parliamentarians and one of the most important powers we have is the ability to hold the executive to account through parliamentary pqs but these pqs are now being treated with contempt by the services. questions are not receiving proper answers they are evasive incomplete and dismissive and the timescale for answering is frequency exceeded. rule.
in other terms it will create new jobs and new financing opportunities for infrastructure investments and smes.
in other terms it will create new jobs and new financing opportunities for infrastructure investments and small businesses.
pollen is present in honey independently of the action of the beekeeper who has no control whatsoever over the presence of pollen in the final product.
Pollen is present in honey independently of the action of the gardener who has no control whatsoever over the presence of pollen in the final product.
direction. but a treaty change is not the right way to deal with an immediate financial crisis. so we have to get the different time perspectives
Direction. But a treaty change is not the right way to deal with an immediate financial crisis. So we have to get the different time perspectives.
this coherence and compatibility can only be achieved through the community institutions because they are the ones mandated to act in the interests of all our member states and our citizens in a rule based indeed treaty based
This coherence and compatibility can only be achieved through the community institutions because they are the ones mandated to act in the interests of all our member states and our citizens in a rule based indeed treaty based.
so as i have already emphasised in previous discussions we have to make sure that we achieve better implementation of the existing guidelines with the evaluation of existing policies developing more effective protection. finally i strongly encourage member states
So as I have already emphasised in previous discussions we have to make sure that we achieve better implementation of the existing guidelines with the evaluation of existing policies developing more effective protection. Finally I strongly encourage member states.
we trust that the commission will carefully assess whether it has been correctly implemented by all member states and will take any appropriate measures in the case of any breach.
we trust that the committee will carefully assess whether it has been correctly implemented by all member regions and will take any appropriate measures in the case of any breach.
your debates and the work of your committees have also furnished many of the ideas that have shaped this process and in some cases decisively improved the outcome.
your debates and the work of your committees have also furnished many of the ideas that have shaped this process and in some instances decisively improved the outcome.
we have not yet left the crisis fully behind us;
we have not yet left the challenge fully behind us;
the legislative proposal by the commission on collective redress does not however make the call in this report redundant.
The legislative proposal by the authority on collective redress does not however make the call in this report redundant.
some say clean coal.
Some say clean energy.
madam president journalism is a cornerstone of democracy holding those in power to account. the appointment of editor in chief of independent news media stephen rae to the eu expert group on fake news beggars belief.
Madam president journalism is a cornerstone of democracy holding those in power to account. The appointment of editor in chief of independent news media john doe to the global expert group on fake news beggars belief.
human. there are no other criteria that should
Human. There are no other criteria that should.
what for example does it tell us about the commission's future intentions?
What for example does it tell us about the authority's future intentions?
however some amendments would restrict their interventions to cases of discrimination and impede interventions to correct other undesirable distortions of the market.
However, some amendments would restrict their interventions to cases of discrimination and impede interventions to correct other undesirable distortions of the market.
that is why we would like to ask the commissioner to confirm that there will be no duplication of tasks between the observatory and the group of experts which the commission would like to establish according to the action plan on the enforcement of intellectual property rights and that
That is why we would like to ask the commissioner to confirm that there will be no duplication of tasks between the observatory and the group of experts which the commission would like to establish according to the action plan on the enforcement of intellectual property rights and that.
this report would give better protection by ensuring that passengers subject to long delays receive the same rights to compensation as those suffering cancellations. it would also extend the right to accommodation in these cases and emphasise support for disabled passengers.
This report would give better protection by ensuring that passengers subject to long delays receive the same rights to compensation as those suffering cancellations. It would also extend the right to accommodation in these cases and emphasize support for disabled passengers.
in recent years regional airports have begun to pursue commercial objectives and are competing with each other to attract air traffic.
In recent years, regional airports have begun to pursue commercial objectives and are competing with each other to attract air traffic.
as previous speakers have said the importance of the report cannot be overstated in view of the fact that a mortgage is often the most important and longest financial commitment a family makes.
As previous speakers have said, the importance of the report cannot be overstated in view of the fact that a mortgage is often the most important and longest financial commitment a family makes.
in saying that i am conscious that success would require genuine political will on both sides and that the longterm interests require functioning political institutions within the country rather than reliance on external assistance.
In saying that, I am conscious that success would require genuine political will on both sides and that the long-term interests require functioning political institutions within the country rather than reliance on external assistance.
looking to the future we will have to modernise the budget significantly and modernisation is not only on the expenditure side.
Looking to the future we will have to modernize the budget significantly and modernization is not only on the expenditure side.
level. some countries should do more to ensure that government services and regulations support industry's
Level. Some countries should do more to ensure that government services and regulations support industry's.
indeed the objective is fully in line with the commission's belief that we have to create a dynamic and inclusive labour market.
Indeed, the objective is fully in line with the commission's belief that we have to create a dynamic and inclusive labour market.
the commission is committed to ensuring that the developing countries which have the ambition for reform are supported in this difficult
The commission is committed to ensuring that the developing countries which have the ambition for reform are supported in this difficult.
the litmus test of any civilised society as people listening in the visitors' gallery will tell you is not how we treat the majority but how we treat the minorities and in that instance some member states are sadly lacking.
The litmus test of any civilized society as people listening in the visitors' gallery will tell you is not how we treat the majority but how we treat the minorities and in that instance some member states are sadly lacking.
yes this proposal could have been shaped as a powerful instrument to say to these member states you go through difficult times and we will support you. unfortunately this chance has been missed.
Yes, this proposal could have been shaped as a powerful instrument to say to these member states you go through difficult times and we will support you. Unfortunately, this chance has been missed.
right. i describe it as being this simple for human rights to apply to you you simply have to be here and
Right. I describe it as being this simple for human rights to apply to you you simply have to be here and.
the failure of our airlines and our airports to deal with a few centimetres of snow in a few member states caused devastating delay disruption and despair for travellers.
The failure of our airlines and our airports to deal with a few centimeters of snow in a few member states caused devastating delay disruption and despair for travelers.
at the same time we must recognise that oda alone will not be nearly enough to finance such a far reaching broad new global development agenda. therefore we must envisage a new more strategic and functional additional role for
At the same time we must recognize that ODA alone will not be nearly enough to finance such a far reaching broad new global development agenda. Therefore we must envisage a new more strategic and functional additional role for.
but that is not the economic governance we
but that is not the economic governance we.
if the latter then there are a few things we are going to have to
if the latter then there are a few things we are going to have to.
this ambitious package in particular the measures to increase competiveness and to liberalise the economy now needs implementation.
This ambitious package in particular the measures to increase competitiveness and to liberalise the economy now needs implementation.
the environmental dimension of these challenges is closely interconnected with fundamental socio economic factors as well as issues such as widespread poverty corruption human rights abuses stability and security.
The environmental dimension of these challenges is closely interconnected with fundamental socio-economic factors as well as issues such as widespread poverty corruption human rights abuses stability and security.
on the prevention and protection of victims of gender based violence.
On the prevention and protection of victims of gender-based violence.
policy. yet we need a policy
Policy. Yet we need a policy.
thank you for your support.
Thank you for your assistance.
an important part of doing this is by ensuring that our workforce feels confident and indeed that foreign visitors feel confident to travel by air.
A significant aspect of doing this is by ensuring that our workforce feels assured and indeed that international visitors feel secure to travel by air.
so maybe we should look at long term management plans as well as just immediate funding.
So perhaps we should consider long-term management strategies as well as just immediate financing.
there will be many new members.
There will be numerous new participants.
this is a major achievement.
This is a significant accomplishment.
in this context the commission is also willing to consider opening investigations based on the threat of injury.
In this context, the commission is also willing to consider opening investigations based on the threat of harm.
the legislation does not require clarification or improvement.
The regulation does not require clarification or enhancement.
i could of course provide you with the website.
I could, of course, provide you with the webpage.
where is the commission's programme on this key growth instrument?
Where is the commission's plan on this key growth tool?
they are not there for intermediaries or the interlopers to interact with one another.
They are not there for intermediaries or the outsiders to interact with one another.
the commission wants to ensure a dialogue between the actors to make sure we are all ready for the big day in.
The commission wants to ensure a dialogue between the participants to make sure we are all ready for the big event.
a fully functioning internal energy market connected to the global market is the key to security of supply and to the long term competitiveness of our industry.
A fully functioning internal energy market connected to the international market is the key to security of supply and to the long-term competitiveness of our industry.
this time it is not only about political dialogue or its absence;
This time, it is not only about political dialogue or its absence.
remove the common fisheries policies from their shores and allow them to sell their goods at a rate that suits them.
Remove the common fisheries regulations from their shores and allow them to sell their products at a rate that suits them.
the president and his companions must cease their actions.
The leader and his companions must cease their actions.
for example these concern the use and translation of the term gender.
For instance, these concern the use and translation of the term identity.
our hope was to pave the way for the digital single market by removing borders barriers and burdens but these rules are not future proof and could actually be a break to innovation.
Our hope was to pave the way for the digital single market by removing borders, obstacles, and burdens, but these rules are not future-proof and could actually be a hindrance to innovation.
mr president this report seeks to generate a regulation to restrict members of the public from purchasing and to require notification concerning sales of a large number of substances which are commonly used for legitimate purposes.
Mr. President, this report seeks to generate a regulation to restrict members of the public from purchasing and to require notification concerning sales of a large number of substances which are commonly used for legitimate purposes.
it is our duty to protect children. we need to focus on prevention the quality of care and protection. we must reinforce our fight against the criminals mobilise and inform public opinion and put pressure on member
It is our duty to protect children. We need to focus on prevention, the quality of care and protection. We must reinforce our fight against the offenders, mobilise and inform public opinion, and put pressure on members.
what chance is there right now of a stronger and more democratic set of institutions emerging from a revised treaty?
What chance is there right now of a stronger and more democratic set of institutions emerging from a modified agreement?
at the same time we also need to build much more powerful instruments to cope with citizens' concerns.
At the same time, we also need to build much more powerful tools to cope with citizens' concerns.
everyone agrees that we need to do something; perhaps not everyone agrees on the measures we need to take or the speed with which we will do it.
Everyone agrees that we need to do something; perhaps not everyone agrees on the actions we need to take or the speed with which we will do it.
fighting for equality not just for gay men and lesbians and bisexuals and transgender people but for people on the basis of their age their religion their belief their gender anything that is perceived to be different that could be used to take equality away from them.
Fighting for equality not just for gay men and lesbians and bisexuals and transgender people, but for people on the basis of their age, their religion, their belief, their identity, anything that is perceived to be different that could be used to take equality away from them.
we may need best practices or guidelines in specific sectors such as energy and health which make increasing use of personal data and need to develop privacyfriendly solutions.
We may need best practices or guidelines in specific sectors such as energy and health, which make increasing use of personal data and need to develop privacy-friendly solutions.
the current law has not been one of the easiest to implement particularly concerning extraordinary circumstances.
The current regulation has not been one of the easiest to implement, particularly concerning extraordinary circumstances.
right. this brings me to my concluding remark on our
Correct. This brings me to my concluding remark on our.
we pushed for more compliance checks yes;
We pushed for more compliance reviews, yes.
they are doing that because they want to push forward their ideology of taking away our rights.
They are doing that because they want to push forward their agenda of taking away our rights.
offences relating to participation in a criminal organisation.
Offences relating to participation in a criminal group.
and yes of course we have to deal with the root causes but let us accept that our own failure in being able to help do so means that we have an obligation to help.
And yes, of course, we have to deal with the root causes, but let us accept that our own failure in being able to help do so means that we have an obligation to assist.
in addition the right of compensation will apply to the victims who have actually suffered the harm including those who had no direct dealings with an infringer because they were further down the supply chain.
In addition, the right of compensation will apply to the victims who have actually suffered the harm, including those who had no direct dealings with an infringer because they were further down the supply chain.
the indigenous people and local communities have therefore to be part of the solution.
The native people and local communities have therefore to be part of the solution.
it must also be willing to listen and able to compromise.
It must also be willing to listen and able to negotiate.
therefore packaging techniques such as modified atmosphere packaging and innovations such as active and intelligent packaging can ameliorate this. my party and i therefore believe that plastic packaging which cannot be reused should be made of a substance that can be recycled.
Therefore, packaging techniques such as modified atmosphere packaging and innovations such as active and intelligent packaging can improve this. My party and I therefore believe that plastic packaging which cannot be reused should be made of a substance that can be recycled.
area. we need more integration more discipline more convergence.
Region. We need more integration, more discipline, more convergence.
this is critically important at this
This is critically important at this.
identifying the balance and the right of access to data on the part of law enforcement authorities.
Identifying the balance and the right of access to data on the part of regulatory authorities.
you are threatening;
You are endangering.
the same is true for climate action policy in relation to energy
The same is true for climate action strategy in relation to energy.
this is why we have included these questions in the green paper.
This is why we have included these inquiries in the green document.
this will contribute to our common strategic objective of achieving a deeper and fairer internal market while fostering innovation with a strong positive impact on jobs and growth.
This will contribute to our common strategic objective of achieving a deeper and fairer internal market while fostering innovation with a strong positive impact on employment and growth.
allow me to give you another concrete example where our innovative and financing products make an impact in this case in a country hit by the financial crisis.
Allow me to give you another concrete example where our innovative and financing products make a difference, in this case, in a nation hit by the financial crisis.
the resources we need for infrastructure cannot be covered by public money.
The resources we need for infrastructure cannot be covered by government funds.
we always say there is no security without development but there is no development without security.
We always say there is no safety without development, but there is no development without safety.
smes and as such in the real economy.
SMEs and, as such, in the actual economy.
i want to assure this house that work on abolishing the death penalty is a personal priority for
I want to assure this house that work on abolishing the death penalty is a personal priority for.
as a former journalist i realise the indispensable role of a free press in any state grounded in the rule of law.
As a former journalist, I realise the indispensable role of a free press in any nation grounded in the rule of law.
we also need to be pragmatic and accept that we have to respond together united to this crisis.
We also need to be pragmatic and accept that we have to respond together, united to this crisis.
our relations with our eastern neighbours are not detrimental to relations with the other neighbours. we never sought exclusivity in our relations.
Our relations with our western neighbours are not detrimental to relations with the other neighbours. We never sought exclusivity in our relations.
we have the responsibility to do more and in particular we need to address the taboos that surround infectious diseases.
We have the responsibility to do more, and in particular, we need to address the taboos that surround infectious diseases.
oda by using it in a more catalytic manner to engage and leverage other financial and non financial means of implementation that would suffice to cover such a demanding new sdg agenda.
Oda by using it in a more catalytic manner to engage and leverage other financial and non-financial means of implementation that would suffice to cover such a demanding new SDG agenda.
of a mouse. political processes even if they are working at their most rapid cannot deliver
Of a mouse. Political processes even if they are working at their most rapid cannot deliver.
potential. we must now get down to the business of extracting the biggest added value from every last euro that has been
Potential. We must now get down to the business of extracting the biggest added value from every last euro that has been.
i believe we share the same objective to ensure that the global agreement on financing for development includes ambitious and credible commitments from
I believe we share the same objective to ensure that the global agreement on financing for development includes ambitious and credible commitments from.
we cannot return to the old ways of doing
We cannot return to the old ways of doing.
so how should we
So how should we.
the fact that governments are reluctant to ratify this key instrument shows how little they care about women's safety.
the fact that authorities are hesitant to endorse this crucial tool shows how little they care about women's safety.
these people will not be stopped by any cold sea any fence any
these people will not be stopped by any cold sea any fence any.
we policy makers have raised the stakes by promising to deliver. the challenges are well known;
we policy makers have raised the stakes by promising to deliver. the challenges are well known;.
most mortgages are local to the country from which the applicant derives.
most mortgages are local to the region from which the applicant derives.
renewal. it is clear that growth and prosperity will not be restored
renewal. it is clear that growth and prosperity will not be restored.
would you agree that that is the main strength of this place?
would you agree that that is the main strength of this location?
so prima will fill this critical gap.
so alpha will fill this critical gap.
we cannot be alone in the world in this
we cannot be alone in the world in this.
and by improving access to finance for our
and by improving access to finance for our.
i would like to congratulate her on the eloquent way in which she laid out the reasons why honey has pollen as a constituent
i would like to congratulate her on the eloquent way in which she laid out the reasons why honey has pollen as a constituent.
it. it is a matter of simple common sense and we are delivering it and will continue to deliver
it. it is a matter of simple common sense and we are delivering it and will continue to deliver.
by cutting red tape and reducing regulatory burdens;
by cutting red tape and reducing regulatory burdens.
there is no shortcut which would ignore this value based accession process where conditionality is our main instrument. what i have always expected from this house is that
There is no shortcut which would ignore this value based accession process where conditionality is our main instrument. What I have always expected from this house is that.
effort. we also need to have the major economies
Effort. We also need to have the major economies.
i am very happy about this achievement and your improvements to
I am very happy about this achievement and your improvements to.
some climate change interventions for instance will meet the oda definition. it is therefore important that synergies across various sustainable development objectives can be maximised to ensure that available resources can deliver the maximum
some climate change interventions for instance will meet the oda definition. it is therefore important that synergies across various sustainable development objectives can be maximised to ensure that available resources can deliver the maximum.
i came in here like my colleague over there in good faith. i wanted to listen to the debate;
i came in here like my colleague over there in good faith. i wanted to listen to the debate;.
human trafficking is the fastest growing criminal industry in the world;
human trafficking is the fastest growing criminal industry in the world;.
links are steadily growing with a broad range of other lucrative criminal activities such as drugs or even trafficking in human beings or exploiting technological developments for criminal purposes. huge criminal proceeds are generated
links are steadily growing with a broad range of other lucrative criminal activities such as drugs or even trafficking in human beings or exploiting technological developments for criminal purposes. huge criminal proceeds are generated.
we have to act against the regime and in the interests of the people so it is essential that when we talk about sanctions we understand what effects those sanctions may have on the population. i could referring to the number of arguments that were made give you a very long list of the sanctions we have imposed and yes i want to confirm that we are ready to go even further
we have to act against the regime and in the interests of the people so it is essential that when we talk about sanctions we understand what effects those sanctions may have on the population. i could referring to the number of arguments that were made give you a very long list of the sanctions we have imposed and yes i want to confirm that we are ready to go even further.
either
either.
i stand here fortunate as a gay man and if i chose to be gay is it not interesting that one obviously therefore chooses to be heterosexual?
i stand here fortunate as a gay individual and if i chose to be gay is it not interesting that one obviously therefore chooses to be heterosexual?
so it is great to see that commitment from the commission and leafing through the strategy i must say the analysis is very strong the language is right and the intentions are very very promising.
so it is great to see that commitment from the authority and leafing through the strategy i must say the analysis is very strong the language is right and the intentions are very very promising.
i can assure you that the commission will continue supporting the sector's efforts to become more market orientated and secure its long term sustainability.
i can assure you that the authority will continue supporting the sector's efforts to become more market orientated and secure its long term sustainability.
i found him to be a most charming man who directly to our delegation promised reform.
i found him to be a most charming individual who directly to our delegation promised reform.
too late. the markets have the luxury of moving at the speed of a click
too late. the markets have the luxury of moving at the speed of a click.
so the defence package just presented by the commission is certainly a very important move and we need to be prepared to have that discussion about the package but we know that lasting peace also depends a lot on permanent systemic action for development
so the defence package just presented by the authority is certainly a very important move and we need to be prepared to have that discussion about the package but we know that lasting peace also depends a lot on permanent systemic action for development.
my team has just been meeting with a group of meps to talk further about what more we should do on this.
my team has just been meeting with a group of representatives to talk further about what more we should do on this.
for example in education the minister spoke about education at the meeting of the education ministers.
for example in education the leader spoke about education at the meeting of the education leaders.
this is a priority for the commission and will remain so for the remainder of its mandate.
this is a priority for the authority and will remain so for the remainder of its mandate.
the commission will bring forward these measures as rapidly as possible and propose changes to the legal framework if necessary.
the authority will bring forward these measures as rapidly as possible and propose changes to the legal framework if necessary.
with the revision to this regulation and a new comprehensive list of extraordinary circumstances we can close the loopholes which have prevented passengers including many of my constituents from receiving restitution when delayed by airlines for reasons of poor operational management. in future passengers will also have clear and transparent information on hand luggage allowances and reassurance that they will not be penalised
with the revision to this regulation and a new comprehensive list of extraordinary circumstances we can close the loopholes which have prevented passengers including many of my constituents from receiving restitution when delayed by airlines for reasons of poor operational management. in future passengers will also have clear and transparent information on hand luggage allowances and reassurance that they will not be penalised

too often that is what i see organisations doing and i will not do that with the external action service.
external action servic
Too often that is what I see companies doing and I will not do that with the external action service.
i do not accept responsibility here for what is happening today in this country but we should accept that we have contributed to the conditions where this political crisis has been generated and i ask the current presidency to do better than its predecessors in actually making good the words that she has shared with us tonight.
tonigh
I do not accept responsibility here for what is happening today in this nation but we should accept that we have contributed to the conditions where this political crisis has been generated and I ask the current leadership to do better than its predecessors in actually making good the words that she has shared with us tonight.
i would like to thank the rapporteur mr coelho not only for all his work on schengen on this particular dossier but also for his flexibility when the council proposed having a separate legal instrument to ensure the participation of the uk and ireland in the policing aspects of the sis.
si
i would like to thank the rapporteur mr smith not only for all his work on schengen on this particular dossier but also for his flexibility when the committee proposed having a separate legal instrument to ensure the participation of the usa and ireland in the policing aspects of the sis.
i think mr lechner with this action you have left a stamp on the european parliament and i think we can all thank you for the work you have done in the interests of the citizens of europe.
europ
i think mr johnson with this action you have left a stamp on the world health organization and i think we can all thank you for the work you have done in the interests of the citizens of europe.
accuracy = 95.62234563868017%

In [ ]:
#check if the word required has been changed:
def reverse_list(lists):
    new_list = []
    for i in lists:
        new_list.insert(0, i)
    return new_list

def replaced_words_proximity(start, end):
    end_idx = -1
    close_words = []
    for idx, i in enumerate(start):
        start_idx = i
        if start_idx == end_idx:
            close_words.append(idx)
        end_idx = int(end[idx]) + 1
    return close_words

def closest_find(sentence, target_word, target_idx):
    length = 0
    prev_distance = 1000
    best_idx = 0
    for idx, i in enumerate(sentence.split()):
        length += len(i + " ")
        if i == target_word:
            distance = abs(target_idx - length)
            if distance < prev_distance:
                best_idx = length - len(i)
                prev_distance = distance
    return best_idx

non_replace_wrong = 0
replace_wrong = 0
non_replace_count = 0
replace_count = 0
collate_word_types = {}
remove_list = ["Replace", "wordReplace", "the", "ner", "type", "word", "starting", "from", "character", "to", ",", "with", "a", "dissimilar", ".", "give", "me", "replaced", "sentence", "based", "on", "original"]
for each in json_data:

        original_text = each.get("Original Sentence")
        og_end = len(original_text) - 1

        replaced_text = each.get("Replaced Sentence")
        replaced_end = len(replaced_text)
        og_instruction = each.get("Original NER Instructions")
        print(og_instruction)
        og_instruction = og_instruction.replace(",", "")
        og_instruction = og_instruction.replace(".", "")
        og_instruction = og_instruction.replace(":", "")
        og_instruction = og_instruction.split(" ")
        instruction = [word for word in og_instruction if word not in remove_list]

        itr_count = 0
        types = []
        start = []
        end = []
        print(instruction)
        for i in instruction:
            if itr_count == 0:
                types.append(i)
                itr_count += 1
            elif itr_count == 1:
                start.append(i)
                itr_count += 1
            else:
                end.append(i)
                itr_count = 0
            
        types = reverse_list(types)
        start = reverse_list(start)
        end = reverse_list(end)

        if types == ['']:
            non_replace_count += 1
            if original_text != replaced_text.lower():
                non_replace_wrong += 1
        else:
            check_proximity = replaced_words_proximity(start, end)
            for idx, i in enumerate(end):
                start_idx = int(start[idx])
                end_idx = int(i)
                unchanged_front = original_text[0:start_idx-1].split()[-1]
                original_tbc = original_text[start_idx:end_idx]
                if check_proximity == []:
                    start_replaced_idx = closest_find(replaced_text, unchanged_front, start_idx) + len(unchanged_front)
                    edit_replaced_text = replaced_text[start_replaced_idx:len(replaced_text)-1]
                elif idx in check_proximity:
                    start_replaced_idx = replaced_text.find(changed_text) + len(changed_text)
                    edit_replaced_text = replaced_text[start_replaced_idx:len(replaced_text)-1]
                if original_text[end_idx:og_end].split() != []:
                    unchanged_back = original_text[end_idx:og_end].split()[0]
                    end_replaced_idx = edit_replaced_text.find(unchanged_back)
                    changed_text = edit_replaced_text[0:end_replaced_idx-1]
                if types[idx] in collate_word_types.keys():
                    new = collate_word_types.get(types[idx])
                    new.append(changed_text)
                    collate_word_types[types[idx]] = new
                else:
                    collate_word_types[types[idx]] = [changed_text]
                replace_count += 1
                if original_tbc == changed_text:
                    replace_wrong += 1
accuracy = 100 - (replace_wrong + non_replace_wrong)/(replace_count + non_replace_count)*100
print(f'accuracy = {accuracy}%')
print(f'Non replacement wrongs = {non_replace_wrong}/{non_replace_count}')
print(f'Replacement wrongs = {replace_wrong}/{replace_count}')

Replace the PLACE ner type word, starting from character 41 to character 42, with a dissimilar word.
['PLACE', '41', '42']

['']

['']
Replace the PLACE ner type word, starting from character 174 to character 175, with a dissimilar word.'Replace the ORG ner type word, starting from character 57 to character 78, with a dissimilar word.'Replace the WHEN ner type word, starting from character 4 to character 34, with a dissimilar word.
['PLACE', '174', '175', "word'Replace", 'ORG', '57', '78', "word'Replace", 'WHEN', '4', '34']
Replace the ORG ner type word, starting from character 38 to character 60, with a dissimilar word.
['ORG', '38', '60']

['']
Replace the PLACE ner type word, starting from character 64 to character 69, with a dissimilar word.
['PLACE', '64', '69']

['']
Replace the WHEN ner type word, starting from character 120 to character 128, with a dissimilar word.'Replace the WHEN ner type word, starting from character 48 to character 87, with a dissimilar word.'Replace the OR

For spelled out version:
accuracy = 99.14024717893605%
Non replacement wrongs = 16/552
Replacement wrongs = 0/1309

In [5]:
pprint.pp(collate_word_types)

{'NORP': ['conservatives',
          'environmentalist',
          'eu',
          'ukrainian',
          'ukrainian',
          'american',
          'italian',
          'us',
          'canadian',
          'eu',
          'spanish',
          'american',
          'christian brotherhood',
          'christian brotherhood',
          'sweden',
          'eu',
          'eu',
          'xi',
          'afghan',
          'chinese',
          'italian',
          'spanish',
          'italian',
          'eastern african',
          'italian',
          'spanish',
          'italian',
          'asian',
          'ger',
          'german',
          'asians',
          'venetian',
          'asians',
          'africans',
          'ukrainian',
          'asian',
          'asian',
          'asian',
          'asian',
          'uk',
          'lithuanian governing class or in popular med',
          'canadian',
          ' with a delegation of five representatives of this assembly i

In [ ]:
from wordcloud import WordCloud, STOPWORDS
import matplotlib.pyplot as plt
 
comment_words = ''
stopwords = set(STOPWORDS)
 
for x, y in collate_word_types.items():
    for each in y:
        val = str(each)
        tokens = val.split()
        for i in range(len(tokens)):
            tokens[i] = tokens[i].lower()
        comment_words += " ".join(tokens)+" "
 
wordcloud = WordCloud(width = 800, height = 800,
                background_color ='white',
                stopwords = stopwords,
                min_font_size = 10).generate(comment_words)
                      
plt.figure(figsize = (8, 8), facecolor = None)
plt.imshow(wordcloud)
plt.axis("off")
plt.tight_layout(pad = 0)
 
plt.show()